<a href="https://colab.research.google.com/github/dhruv5903/ColabNBs/blob/main/R2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
%%capture
!git clone https://github.com/AI4Bharat/IndicTrans2.git

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
os.environ['WANDB_DISABLED']='True'

In [ ]:
%%capture
%cd /content/IndicTrans2/huggingface_interface

In [ ]:
%%capture
!python3 -m pip install nltk sacremoses pandas regex mock transformers>=4.33.2 mosestokenizer
!python3 -c "import nltk; nltk.download('punkt')"
!python3 -m pip install bitsandbytes scipy accelerate datasets
!python3 -m pip install sentencepiece

!git clone https://github.com/VarunGumma/IndicTransToolkit.git
%cd IndicTransToolkit
!python3 -m pip install --editable ./
%cd ..

RESTART SESSION

In [ ]:
import torch
from transformers import AutoModelForSeq2SeqLM, BitsAndBytesConfig, AutoTokenizer
from IndicTransToolkit import IndicProcessor

In [ ]:
modelname='ai4bharat/indictrans2-en-indic-dist-200M'

In [ ]:
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(modelname, trust_remote_code=True)
model = AutoModelForSeq2SeqLM.from_pretrained(
    modelname,
    trust_remote_code=True).to(DEVICE)

In [ ]:
input_sentence=["hello, how are you? "]
source_lang='eng_Latn'
target_lang='eng_Latn'
ip = IndicProcessor(inference=True)
BATCH_SIZE=4

In [ ]:
tokenizer.tokenize('eng_Latn tam_Taml hello, how are you?')

['eng_Latn', 'tam_Taml', '▁hel', 'lo', ',', '▁how', '▁are', '▁you', '?']

In [ ]:
for i in range(0, len(input_sentence), BATCH_SIZE):
  translations=[]
  batch = input_sentence[i : i + BATCH_SIZE]
  batch = ip.preprocess_batch(batch, src_lang=source_lang, tgt_lang=target_lang)
  print(i,batch)
  inputs = tokenizer(batch, truncation=True, padding="longest", return_tensors="pt", return_attention_mask=True).to(DEVICE)
  print(inputs)
  with torch.no_grad():
    model = model.to(DEVICE)
    generated_tokens = model.generate(**inputs, use_cache=True, min_length=0, max_length=256, num_beams=5, num_return_sequences=1)
  with tokenizer.as_target_tokenizer():
    decoded_generated_tokens = tokenizer.batch_decode(generated_tokens.detach().cpu().tolist(), skip_special_tokens=True, clean_up_tokenization_spaces=True)
  translations += ip.postprocess_batch(decoded_generated_tokens, lang=target_lang)

0 ['eng_Latn eng_Latn hello , how are you ?']
{'input_ids': tensor([[   4,    4, 7137, 8656,    7,  126,   30,   31,   35,    2]],
       device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1]], device='cuda:0')}


In [ ]:
#Dataset Import
F=open("/content/drive/MyDrive/training_data/train.eng_Latn","r")
k=F.readlines()
en_words=[]
for i in k:
  en_words.append(i.rstrip('\n'))
F.close()
F=open("/content/drive/MyDrive/training_data/train.tam_Taml","r")
k=F.readlines()
tam_words=[]
for i in k:
  tam_words.append(i.rstrip('\n'))
F.close()

In [ ]:
entries=3000

In [ ]:
test_en_words=en_words[:entries]
test_tam_words=tam_words[:entries]

In [ ]:
#Entire Dataset
test_en_tam_dict=dict()
for i in range(len(test_en_words)):
  test_en_tam_dict[test_en_words[i]]=test_tam_words[i]
test_en_tam_dict

{'abacus': 'எண் சட்டம், மணிச்சட்டம்',
 'abbreviation': 'சுருக்கம், சுருக்கக் குறியீடு, குறுக்கம்',
 'aberration': 'பிறழ்ச்சி',
 'chromatic aberration': 'நிறப் பிறழ்ச்சி',
 'coefficient of aberration': 'ஒளிப் பிறழ்ச்சிக் கெழு',
 'constant of aberration': 'பிறழ்ச்சிக் கெழு',
 'diurnal aberration': 'நாளியக்கப் பிறழ்ச்சி',
 'planetary aberration': 'கோள் பிறழ்ச்சி',
 'abridged notation': 'சுருக்கக் குறியீடு',
 'abscissa': 'கிடைஅச்சுத் தொலைவு, கிடைஆயம்',
 'absolute': 'தனி',
 'absolute deviation': 'தனி விலக்கம்',
 'absolute error': 'தனிப்பிழை',
 'absolute line': 'தனிக்கோடு',
 'absolute magnitude of stars': 'விண்மீன்களின் தனி ஒளிர்வுப் பருமை',
 'absolute motion': 'தனி இயக்கம்',
 'absolute point': 'தனிப்புள்ளி',
 'absolute temperature': 'தனி வெப்பநிலை',
 'absolute tensor': 'தனி மீநெறியம்',
 'absolute value': 'தனி மதிப்பு',
 'absolute velocity': 'தனி திசைவேகம், தனி விரைவு',
 'absolutely': 'தனித்த',
 'absolutely continuous function': 'தனித்த தொடர்ச்சியான சார்பு',
 'absolutely convergent series': 

In [ ]:
len(test_en_tam_dict)

2832

In [ ]:
#Handling relation between two words, containing phrases like- ALSO KNOWN AS and SEE
multiple_en_words=[]
multiple_tam_words=[]
other=[]
for i in test_en_words:
  if '(see ' in i:
    multiple_en_words.append(i.split('(see ')[0])
    multiple_tam_words.append(test_en_tam_dict[i])
  elif 'also known as' in i:
    multiple_en_words.append(i.split('also known as')[0].rstrip('('))
    multiple_tam_words.append(test_en_tam_dict[i])
  else:
    other.append(i)

In [ ]:
'''multiple_dict={}
for i in range(len(multiple_tam_words)):
  multiple_dict[multiple_en_words[i]]=multiple_tam_words[i]
multiple_dict'''

'multiple_dict={}\nfor i in range(len(multiple_tam_words)):\n  multiple_dict[multiple_en_words[i]]=multiple_tam_words[i]\nmultiple_dict'

In [ ]:
#Handling english words with its context token
context_en_word=[]
context_en_word_tam_transl=[]
other_other=[]
j=0
for i in other:
  if ',' in i:
    context_en_word.append(i.split(',')[1].lstrip()+' '+i.split(',')[0])
    context_en_word_tam_transl.append(test_en_tam_dict[i])
  else:
    other_other.append(i)

In [ ]:
'''en_comma_dict={}
for i in range(len(context_en_word)):
  en_comma_dict[context_en_word[i]]=context_en_word_tam_transl[i]
en_comma_dict'''

'en_comma_dict={}\nfor i in range(len(context_en_word)):\n  en_comma_dict[context_en_word[i]]=context_en_word_tam_transl[i]\nen_comma_dict'

In [ ]:
other_en_other=[]
other_tam_other=[]
for i in range(len(other_other)):
  other_en_other.append(other_other[i])
  other_tam_other.append(test_en_tam_dict[other_other[i]])

In [ ]:
#Words with multiple tamil translations from the remaining dataset
comma_tam_other=[]
for i in other_en_other:
  if ',' in test_en_tam_dict[i]:
    comma_tam_other.append(i)
#Words with multiple tamil translations from the entire dataset
comma_test_tam_words=[]
for i in test_en_words:
  if ',' in test_en_tam_dict[i]:
    comma_test_tam_words.append(i)
for i in list(set(comma_test_tam_words)-set(comma_tam_other)):
  print(i,':',test_en_tam_dict[i])

In [ ]:
multiple_en_words2=[]
multiple_tam_words2=[]
for i in range(len(multiple_en_words)):
  if len(multiple_tam_words[i].split(', '))>=2:
    for j in range(len(multiple_tam_words[i].split(', '))):
      multiple_en_words2.append(multiple_en_words[i])
      multiple_tam_words2.append(multiple_tam_words[i].split(', ')[j])
  else:
    multiple_en_words2.append(multiple_en_words[i])
    multiple_tam_words2.append(multiple_tam_words[i])

In [ ]:
#dictionary for multiple tamil translations of english words with a.k.a and see phrase
'''multiple_en_words2:multiple_tam_words2'''

'multiple_en_words2:multiple_tam_words2'

In [ ]:
context_en_word2=[]
context_en_word_tam_transl2=[]
for i in range(len(context_en_word)):
  if len(context_en_word_tam_transl[i].split(', '))>=2:
    for j in range(len(context_en_word_tam_transl[i].split(', '))):
      context_en_word2.append(context_en_word[i])
      context_en_word_tam_transl2.append(context_en_word_tam_transl[i].split(', ')[j])
  else:
    context_en_word2.append(context_en_word[i])
    context_en_word_tam_transl2.append(context_en_word_tam_transl[i])

In [ ]:
#dictionary for multiple tamil translations of english and context word pairs
'''context_en_word2:context_en_word_tam_transl2'''

'context_en_word2:context_en_word_tam_transl2'

In [ ]:
other_en_other2=[]
other_tam_other2=[]
for i in range(len(other_en_other)):
  if len(other_tam_other[i].split(', '))>=2:
    for j in range(len(other_tam_other[i].split(', '))):
      other_en_other2.append(other_en_other[i])
      other_tam_other2.append(other_tam_other[i].split(', ')[j])
  else:
    other_en_other2.append(other_en_other[i])
    other_tam_other2.append(other_tam_other[i])

In [ ]:
#dictionary for multiple tamil translations of the remaining english words
'''other_en_other2:other_tam_other2'''

'other_en_other2:other_tam_other2'

In [ ]:
for i in range(len(context_en_word2)):
  other_en_other2.append(context_en_word2[i])
  other_tam_other2.append(context_en_word_tam_transl2[i])
for i in range(len(multiple_en_words2)):
  other_en_other2.append(multiple_en_words2[i])
  other_tam_other2.append(multiple_tam_words2[i])

In [ ]:
training_data_1 = [
    {"source": "eng_Latn tam_Taml "+other_en_other2[i], "target": "tam_Taml eng_Latn "+other_tam_other2[i]} for i in range(len(other_tam_other2))
]

In [ ]:
training_data_1

[{'source': 'eng_Latn tam_Taml abacus',
  'target': 'tam_Taml eng_Latn எண் சட்டம்'},
 {'source': 'eng_Latn tam_Taml abacus',
  'target': 'tam_Taml eng_Latn மணிச்சட்டம்'},
 {'source': 'eng_Latn tam_Taml abbreviation',
  'target': 'tam_Taml eng_Latn சுருக்கம்'},
 {'source': 'eng_Latn tam_Taml abbreviation',
  'target': 'tam_Taml eng_Latn சுருக்கக் குறியீடு'},
 {'source': 'eng_Latn tam_Taml abbreviation',
  'target': 'tam_Taml eng_Latn குறுக்கம்'},
 {'source': 'eng_Latn tam_Taml aberration',
  'target': 'tam_Taml eng_Latn பிறழ்ச்சி'},
 {'source': 'eng_Latn tam_Taml chromatic aberration',
  'target': 'tam_Taml eng_Latn நிறப் பிறழ்ச்சி'},
 {'source': 'eng_Latn tam_Taml coefficient of aberration',
  'target': 'tam_Taml eng_Latn ஒளிப் பிறழ்ச்சிக் கெழு'},
 {'source': 'eng_Latn tam_Taml constant of aberration',
  'target': 'tam_Taml eng_Latn பிறழ்ச்சிக் கெழு'},
 {'source': 'eng_Latn tam_Taml diurnal aberration',
  'target': 'tam_Taml eng_Latn நாளியக்கப் பிறழ்ச்சி'},
 {'source': 'eng_Latn tam_Ta

PANDAS DATAFRAME

In [ ]:
import pandas
en_tam_dataset={'English':other_en_other2, 'Tamil':other_tam_other2}
df=pandas.DataFrame(en_tam_dataset)
df.to_csv('/content/en_tam_dataset.csv')
df

English                                  Tamil
0                       abacus                             எண் சட்டம்
1                       abacus                            மணிச்சட்டம்
2                 abbreviation                              சுருக்கம்
3                 abbreviation                     சுருக்கக் குறியீடு
4                 abbreviation                              குறுக்கம்
...                        ...                                    ...
3197  orientation of a circuit     சுற்றின் (வட்டகையின்) திசைப்போக்கு
3198          oriented simplex           திசைப்போக்குள்ள தனியன் முகம்
3199          short five lemma                  ஐங்குறு துணைத்தேற்றம்
3200  min-cut theorem max-flow  பெருமப் பாய்வு-சிறும வெட்டுத் தேற்றம்
3201       set of measure zero                         சுழி அளவை கணம்

[3202 rows x 2 columns]

In [ ]:
# Add new word-translation pairs
new_tokens = list(set(other_en_other2)) + list(set(other_tam_other2))

In [ ]:
tokenizer.add_tokens(new_tokens)
tokenizer.save_pretrained("/content/custom_tokenizer")

('/content/custom_tokenizer/tokenizer_config.json',
 '/content/custom_tokenizer/special_tokens_map.json',
 '/content/custom_tokenizer/dict.SRC.json',
 '/content/custom_tokenizer/dict.TGT.json',
 '/content/custom_tokenizer/model.SRC',
 '/content/custom_tokenizer/model.TGT',
 '/content/custom_tokenizer/added_tokens.json')

In [ ]:
tokenizer

IndicTransTokenizer(name_or_path='ai4bharat/indictrans2-en-indic-dist-200M', vocab_size=32322, model_max_length=256, is_fast=False, padding_side='left', truncation_side='right', special_tokens={'bos_token': '<s>', 'eos_token': '</s>', 'unk_token': '<unk>', 'pad_token': '<pad>'}, clean_up_tokenization_spaces=True, added_tokens_decoder={
	0: AddedToken("<s>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	1: AddedToken("<pad>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	2: AddedToken("</s>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	3: AddedToken("<unk>", rstrip=False, lstrip=False, single_word=False, normalized=False, special=True),
	665: AddedToken("ant", rstrip=False, lstrip=False, single_word=False, normalized=True, special=False),
	986: AddedToken("year", rstrip=False, lstrip=False, single_word=False, normalized=True, special=False),
	1181: AddedToken("ion", rstrip=False, l

In [ ]:
from transformers import MBartForConditionalGeneration
# Load model
model = MBartForConditionalGeneration.from_pretrained(modelname, ignore_mismatched_sizes=True)

You are using a model of type IndicTrans to instantiate a model of type mbart. This is not supported for all configurations of models and can yield errors.
Some weights of MBartForConditionalGeneration were not initialized from the model checkpoint at ai4bharat/indictrans2-en-indic-dist-200M and are newly initialized: ['model.decoder.embed_positions.weight', 'model.encoder.embed_positions.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of MBartForConditionalGeneration were not initialized from the model checkpoint at ai4bharat/indictrans2-en-indic-dist-200M and are newly initialized because the shapes did not match:
- lm_head.weight: found shape torch.Size([122672, 512]) in the checkpoint and torch.Size([122672, 1024]) in the model instantiated
- model.decoder.embed_tokens.weight: found shape torch.Size([122672, 512]) in the checkpoint and torch.Size([122672, 1024]) in the model instantiated
- model.de

In [ ]:
# Resize model embeddings to include new tokens
model.resize_token_embeddings(len(tokenizer))

MBartScaledWordEmbedding(80485, 1024, padding_idx=1)

In [ ]:
tokenizer.tokenize('eng_Latn tam_Taml Hi, This is an abacus')

['eng_Latn', 'tam_Taml', '▁Hi', ',', '▁This', '▁is', '▁an', 'abacus']

In [ ]:
preprocessed_data=[]
for pair in training_data_1:
  print(pair["source"].split(" ",2))
  input=tokenizer(pair["source"], truncation=True, padding="max_length", max_length=20, return_tensors="pt")
  targets=tokenizer(pair["target"], truncation=True, padding="max_length", max_length=20, return_tensors="pt")
  input['labels']=targets['input_ids']
  print(input)
  preprocessed_data.append(input)



Streaming output truncated to the last 5000 lines.
['eng_Latn', 'tam_Taml', 'bijective function']
{'input_ids': tensor([[    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     4,    27, 38431,     2]]), 'attention_mask': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1]]), 'labels': tensor([[    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,    27,     4, 68115,     2]])}
['eng_Latn', 'tam_Taml', 'bounded function']
{'input_ids': tensor([[    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,     4,    27, 53877,     2]]), 'attention_mask': tensor([[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1]]), 'labels': tensor([[    1,     1,     1,     1,     1,     1,     1,     1,     1,     1,
             1,     1,     1,     1,     1,     1,    27,     4, 72

WANDB API 425cb8721c559edce5458b3d6744b577c07e3695

In [ ]:
from transformers import Trainer, TrainingArguments
import torch
train_dataset = preprocessed_data
# Set up training arguments with an evaluation strategy for downstream task training
training_args = TrainingArguments(
    output_dir="/content/indictrans_vocab_tuned",
    learning_rate=5e-5,
    eval_strategy="no",
    per_device_train_batch_size=32,
    num_train_epochs=2,
    weight_decay=0.01,
    fp16=torch.cuda.is_available(),
    save_total_limit=2,
)

# Initialize the Trainer with both training and validation datasets
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset
)

# Train (fine-tune) the model on your downstream translation task
trainer.train()

# Save the fine-tuned model for later inference
trainer.save_model("/content/fine_tuned_english_tamil")

In [ ]:
model=MBartForConditionalGeneration.from_pretrained("/content/fine_tuned_english_tamil", ignore_mismatched_sizes=True)

In [ ]:
input_sentence=["what is your name?"]
source_lang='eng_Latn'
target_lang='tam_Taml'
ip = IndicProcessor(inference=True)
BATCH_SIZE=4

In [ ]:
for i in range(0, len(input_sentence), BATCH_SIZE):
  translations=[]
  batch = input_sentence[i : i + BATCH_SIZE]
  batch = ip.preprocess_batch(batch, src_lang=source_lang, tgt_lang=target_lang)
  print(i,batch)
  inputs = tokenizer(batch, truncation=True, padding="longest", return_tensors="pt", return_attention_mask=True).to(DEVICE)
  print(inputs)
  with torch.no_grad():
    model = model.to(DEVICE)
    generated_tokens = model.generate(**inputs, use_cache=True, min_length=0, max_length=256, num_beams=5, num_return_sequences=1)
  with tokenizer.as_target_tokenizer():
    decoded_generated_tokens = tokenizer.batch_decode(generated_tokens.detach().cpu().tolist(), skip_special_tokens=True, clean_up_tokenization_spaces=True)
  translations += ip.postprocess_batch(decoded_generated_tokens, lang=target_lang)

0 ['eng_Latn tam_Taml what is your name ?']
{'input_ids': tensor([[  4,  27,  84,  13,  63, 281,  35,   2]], device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1]], device='cuda:0')}


/usr/local/lib/python3.11/dist-packages/transformers/tokenization_utils_base.py:3970: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


In [ ]:
translations

['']